In [1]:
#TO DOs
# 1. Remove non-printable characters
# def replace_trash(unicode_string):
#      for i in range(0, len(unicode_string)):
#          try:
#              unicode_string[i].encode("ascii")
#          except:
#               #means it's non-ASCII
#               unicode_string=unicode_string[i].replace(" ") #replacing it with a single space
#      return unicode_string
# 2. Fetch L0... L4 data automatically from dictionary.txt

In [1]:
import pandas as pd
import numpy as np

# header=0 doens't work, header=None simply inserts intergers as column names
df_raw = pd.read_csv(f'./ticdata2000.txt', sep='\t', header=None, low_memory=False)

In [2]:
def display_all(df):
    with pd.option_context("display.max_rows", 1000, "display.max_columns", 1000): 
        display(df)

In [3]:
def get_item_description(start_row, end_row, from_nth_field_onward):
    """
    # RETURN: A list of extracted item names
    # start_row: Starting row number of dictionary.txt
    # end_row: Ending row number of dictionary.txt
    # from_nth_field_onward: Take out a n-th field, delimited by space, and further to the right
    """
    
    # Thought of returning a ndarray but a "DeprecationWarning: 
    #  "using a non-integer array as obj in delete will result in an error in the future"
    import subprocess
    
    unix_shell_command = 'awk \'NR>={0}&&NR<={1}\' "./dictionary.txt" | cut -d\  -f{2}- '.format(start_row, end_row, from_nth_field_onward)
    
    headers = subprocess.check_output(unix_shell_command, shell=True)
    
    #headers = subprocess.check_output('awk \'NR>=' + str(start_row) + '&&NR<=' + str(end_row) + '\' "./dictionary.txt" | cut -d\  -f3- ', shell=True)
    #headers = subprocess.check_output('awk \'NR>=4&&NR<=89\' "./dictionary.txt" | cut -d\  -f3- ', shell=True)
    # awk \'NR>=4&&NR<=89\' "./dictionary.txt" => take lines between 4 and 89, both incluive
    #  (NOTE: escape character of "\" before ')
    # cut -d\  -f3- => delimiter of a single space with escape character of "\" and
    #  taking in the 3rd field onwards until end of the line
    # This returns byte string e.g., b'Customer Subtype see L0\nNumber of...'

    # Alternative to 'subprocess.check_output' is as follows:
    # import os
    # os.system("command")

    header_list = "".join(map(chr, headers)).split('\n')
    # "".join(map(chr, headers)) => convert bytes to a string
    # .split('\n') => put the produced string into a list delimited by a line feed

    header_list.pop()
    # Unfortuantely this leaves a zero-string list item at the very end i.e., (''), so take it out

    return header_list

In [4]:
list_of_column_names = get_item_description(4, 89, 3)
df_raw.columns = list_of_column_names

In [5]:
df_raw

Customer Subtype see L0  Number of houses 1  10  \
0                          33                        1   
1                          37                        1   
2                          37                        1   
3                           9                        1   
4                          40                        1   
5                          23                        1   
6                          39                        2   
7                          33                        1   
8                          33                        1   
9                          11                        2   
10                         10                        1   
11                          9                        1   
12                         33                        1   
13                         41                        1   
14                         23                        1   
15                         33                        1   
16                         38                        1   
17                         22                        2   
18                         13                        1   
19                         31                        1   
20                         33                        1   
21                         33                        2   
22                         13                        1   
23                         34                        2   
24                         13                        2   
25                         33                        1   
26                         37                        1   
27                         40                        1   
28                         31                        1   
29                         33                        2   
...                       ...                      ...   
5792                       13                        1   
5793                       30                        1   
5794                       33                        1   
5795                       22                        1   
5796                       39                        1   
5797                        8                        1   
5798                       27                        1   
5799                        9                        1   
5800                       31                        1   
5801                        3                        1   
5802                        3                        1   
5803                       36                        1   
5804                       23                        1   
5805                       33                        1   
5806                       38                        2   
5807                       38                        2   
5808                       31                        1   
5809                       35                        1   
5810                       33                        1   
5811                       39                        1   
5812                       40                        1   
5813                        3                        1   
5814                        1                        1   
5815                       13                        1   
5816                        3                        1   
5817                       36                        1   
5818                       35                        1   
5819                       33                        1   
5820                       34                        1   
5821                       33                        1   

      Avg size household 1  6  Avg age see L1  Customer main type see L2  \
0                            3               2                          8   
1                            2               2                          8   
2                            2               2                          8   
3                            3               3                          3   
4                       

In [6]:
def fetch_list_item(nd_array, keyword, from_nth_index = 0):
    """
    RETURN: A tuple of matched item AND index number 
    Fetch column name according to the passed-in 'keyword'
    Perform "exact" search to see if string match AT the end of string ONLY
    """
    
    for index, item in enumerate(nd_array):
        if index >= from_nth_index:
            if item[-len(keyword):] == keyword:
                return index, item
    return None

In [8]:
# test = get_item_description(95, 135, 2)

# #sorted(test)
# print(test)

def remove_duplicate_and_renumber_dictionary(df_series, dictionary):
    """
    RETURN: A list without a duplicate
    """
    #nd_array_data = df_raw['Customer Subtype see L0'].to_numpy()
    nd_array_data = df_series.to_numpy()
    # Create a ndarray from a DataFrame column

    print(nd_array_data)

    for index, item in enumerate(dictionary):
        print(str(index) + '\t' + item + '\t')

        if dictionary.count(item) > 1:
            # Locate the index of the OTHER duplicate, to be left and aligned, from the beginning of the list
            duplicate_num, _ = fetch_list_item(dictionary, item, index+1)

            print('\t'+ _ + '\t' + str(duplicate_num))

            # Replace all the index(s) of the item number to that(those) of the OTHER duplicate
            np.where(nd_array_data==index, duplicate_num, nd_array_data) 

            # The higher-numbered items must be re-numbered
            if item != dictionary[-1]:
                # Only when it's NOT the very last item
                nd_array_data[nd_array_data >= index + 1] -= 1

            # Take it out from both name list and index list
            dictionary.pop(index)
            print(index)
            print(dictionary)
            #test = np.delete(idx, test)
            # DeprecationWarning: in the future out of bounds indices will raise an error instead of being ignored by `numpy.delete`.
            nd_array_data = np.delete(index, nd_array_data)
        
    return dictionary
#age_list = df["age"].tolist()
#df['new_col'] = mylist

#df_raw['Customer Subtype see L0'].cat.set_categories(get_item_description(95, 135, 2), ordered=True, inplace=True)

#df_raw.ftypes

In [7]:
def change_column_type_from_int64_to_category():
    """
    Format DataFrame by replacing 'pure' indices in dictionary.txt with meaningful descriptions
    """
    
    category_cols = [[0, 1, 95, 135], 
                     [1, 1, 140, 145], 
                     [2, 1, 150, 159], 
                     [3, 0, 164, 173], 
                     [4, 0, 178, 187]]
    # 1st element: A number whose table in the dictionary.txt describes further e.g., L0, L1, and L2
    # 2nd element: N-based index in the dictionary.txt. Where it's 1 
    #              we subtract 1 from the original data to make it zero(0)-based, so as to suit indexes of category type
    # 3rd element: Starting row number of dictionary.txt
    # 4th element: Ending row number of dictionary.txt

    for col in category_cols:
        res = fetch_list_item(list_of_column_names, "see L" + str(col[0]), 0)
        if res is not None:
            print(res)
            index, item = res

            if col[1] == 1:
                df_raw[item] = df_raw[item] - 1

            #df_raw[item] = df_raw[item].select_dtypes(include=['int64']).astype('category')
            #df_raw[item] = df_raw[item].astype('category')

            corrected_dictionary = remove_duplicate_and_renumber_dictionary(df_raw[item], get_item_description(col[2], col[3], 2))
            print(item)
            print(corrected_dictionary)
            
            # With a column full of integers, just passing a list of string (name) corresponding to each integer by its index does NOT work
            # Rather, populate the column first with string, convert it as category, and then 'set_categories'
            
            # Create a new column???
            df_raw[item] = df_raw[item][df_raw[item]== corrected_dictionary.index()
            
            df_raw[item] = df_raw[item].astype('category')
            df_raw[item].cat.set_categories(corrected_dictionary, ordered=True, inplace=True)

In [9]:
change_column_type_from_int64_to_category()

(0, 'Customer Subtype see L0')
[32 36 36 ... 32 33 32]
0	High Income, expensive child	
1	Very Important Provincials	
2	High status seniors	
3	Affluent senior apartments	
4	Mixed seniors	
	Mixed seniors	31
4
['High Income, expensive child', 'Very Important Provincials', 'High status seniors', 'Affluent senior apartments', 'Career and childcare', "Dinki's (double income no kids)", 'Middle class families', 'Modern, complete families', 'Stable family', 'Family starters', 'Affluent young families', 'Young all american family', 'Junior cosmopolitan', 'Senior cosmopolitans', 'Students in apartments', 'Fresh masters in the city', 'Single youth', 'Suburban youth', 'Etnically diverse', 'Young urban have-nots', 'Mixed apartment dwellers', 'Young and rising', 'Young, low educated ', 'Young seniors in the city', 'Own home elderly', 'Seniors in apartments', 'Residential elderly', 'Porchless seniors: no front yard', 'Religious elderly singles', 'Low income catholics', 'Mixed seniors', 'Lower class la

/home/to/miniconda3/envs/caravan/lib/python3.6/site-packages/ipykernel_launcher.py:36: DeprecationWarning: in the future out of bounds indices will raise an error instead of being ignored by `numpy.delete`.


AttributeError: Can only use .cat accessor with a 'category' dtype

In [12]:
display_all(df_raw)

Customer Subtype see L0  Number of houses 1  10  \
0                        NaN                        1   
1                        NaN                        1   
2                        NaN                        1   
3                        NaN                        1   
4                        NaN                        1   
5                        NaN                        1   
6                        NaN                        2   
7                        NaN                        1   
8                        NaN                        1   
9                        NaN                        2   
10                       NaN                        1   
11                       NaN                        1   
12                       NaN                        1   
13                       NaN                        1   
14                       NaN                        1   
15                       NaN                        1   
16                       NaN                        1   
17                       NaN                        2   
18                       NaN                        1   
19                       NaN                        1   
20                       NaN                        1   
21                       NaN                        2   
22                       NaN                        1   
23                       NaN                        2   
24                       NaN                        2   
25                       NaN                        1   
26                       NaN                        1   
27                       NaN                        1   
28                       NaN                        1   
29                       NaN                        2   
30                       NaN                        2   
31                       NaN                        1   
32                       NaN                        1   
33                       NaN                        1   
34                       NaN                        2   
35                       NaN                        1   
36                       NaN                        1   
37                       NaN                        1   
38                       NaN                        1   
39                       NaN                        2   
40                       NaN                        1   
41                       NaN                        1   
42                       NaN                        1   
43                       NaN                        1   
44                       NaN                        1   
45                       NaN                        1   
46                       NaN                        1   
47                       NaN                        1   
48                       NaN                        1   
49                       NaN                        2   
50                       NaN                        1   
51                       NaN                        1   
52                       NaN                        1   
53                       NaN                        1   
54                       NaN                        2   
55                       NaN                        2   
56                       NaN                        1   
57                       NaN                        1   
58                       NaN                        1   
59                       NaN                        1   
60                       NaN                        1   
61                       NaN                        1   
62                       NaN                        1   
63                       NaN                        2   
64                       NaN                        1   
65                       NaN                        1   
66                       NaN                        1   
67                       NaN                        1   
68                       NaN                        1   
69             